# Displaying the horizons and ergosurfaces of Kerr spacetime

This Jupyter notebook illustrates some applications of SageMath functionalities in general relativity, specifically in deriving and displaying the horizons and ergosurfaces of Kerr spacetime. Most of the involved tools have been developed through the [SageManifolds project](https://sagemanifolds.obspm.fr/).

**Rogerio T. Cavalcanti**

It requires the SageMath version at least equal to 9.2.

In [1]:
version()

'SageMath version 9.5.beta4, Release Date: 2021-10-19'

In [2]:
%display latex

In [3]:
Parallelism().set(nproc=8)

## Kerr spacetime in Boyer–Lindquist coordinates

In [4]:
a = var('a', domain='positive')
M.<t, r, th, ph> = manifolds.Kerr(m=1, a=a, coordinates='BL')
BL = M.default_chart()

In [5]:
g = M.metric()
g.display_comp()

g_t,t = 2*r/(a^2*cos(th)^2 + r^2) - 1 
g_t,ph = 2*a*r*sin(th)^2/(a^2*cos(th)^2 + r^2) 
g_r,r = (a^2*cos(th)^2 + r^2)/(a^2 + r^2 - 2*r) 
g_th,th = a^2*cos(th)^2 + r^2 
g_ph,t = 2*a*r*sin(th)^2/(a^2*cos(th)^2 + r^2) 
g_ph,ph = (2*a^2*r*sin(th)^2/(a^2*cos(th)^2 + r^2) + a^2 + r^2)*sin(th)^2

### Metric singularities and ergosurfaces

- The $g_{tt},g_{t\phi}$ and $g_{\phi\phi}$ components are singular at the singular ring $a^2\cos^2\theta +r^2=0$, that is $r=0$ and $\theta =\frac{\pi}{2}$ (physical singularity, as checked below)

In [6]:
singular_ring = {r:0, th:pi/2}

- Singular surfaces on $\displaystyle ({g_{rr}})^{-1} = 0$ (Horizons)

In [7]:
horizons = solve(1/g[1,1].expr()==0,r,solution_dict=True)
horizons

[{r: -sqrt(-a^2 + 1) + 1}, {r: sqrt(-a^2 + 1) + 1}]

In [8]:
inner_horizon, outer_horizon = horizons

- The Ergosurfaces are the regions of vanishing $K_\mu K^\mu$, where $K$ the Killing vector field $K = \frac{\partial}{\partial t }$.

In [9]:
K = M.vector_field(1,0,0,0, name='K')
K.display()

K = ∂/∂t

Checking that $K$ is a Killing vector field $(\mathcal{L}_{_K}g = 0)$

In [10]:
g.lie_derivative(K) == 0

True

In [11]:
g(K,K).display()

g(K,K): M → ℝ
   (t, r, th, ph) ↦ 2*r/(a^2*cos(th)^2 + r^2) - 1

In [12]:
ergosurfaces = solve(g(K,K).expr(),r,solution_dict=True)
ergosurfaces

[{r: -sqrt(-a^2*cos(th)^2 + 1) + 1}, {r: sqrt(-a^2*cos(th)^2 + 1) + 1}]

In [13]:
inner_ergo, outer_ergo = ergosurfaces

List of surfaces

In [14]:
surfaces_param = [outer_ergo,outer_horizon,inner_horizon,inner_ergo,singular_ring]

## Rational polynomial coordinates

In rational polinomial coordinates all components of the Kerr metric are rational polynomials, which in principle make it easyer to handle. We are going to use such coordinates for checking the Kretschmann scalar over the horizon and ergosurfaces of the spacetime.

In [15]:
RP.<t, r, ch, ph> = M.chart(r't:(-oo,+oo) r:(0,+oo) ch:(-1,1):\chi ph:(-pi,pi):periodic:\phi')

Transition map from Boyer–Lindquist coordinates to rational polynomial coordinates and its inverse.

In [16]:
BL_to_RP = BL.transition_map(RP, [t, r, cos(th), ph])
BL_to_RP.display()

t = t
r = r
ch = cos(th)
ph = ph

In [17]:
BL_to_RP.set_inverse(t, r, acos(ch), ph)
BL_to_RP.inverse().display()

t = t
r = r
th = arccos(ch)
ph = ph

In [18]:
g.display_comp(RP.frame(),RP)

g_t,t = -(a^2*ch^2 + r^2 - 2*r)/(a^2*ch^2 + r^2) 
g_t,ph = -2*(a*ch^2 - a)*r/(a^2*ch^2 + r^2) 
g_r,r = (a^2*ch^2 + r^2)/(a^2 + r^2 - 2*r) 
g_ch,ch = -(a^2*ch^2 + r^2)/(ch^2 - 1) 
g_ph,t = -2*(a*ch^2 - a)*r/(a^2*ch^2 + r^2) 
g_ph,ph = -(a^4*ch^4 - a^4*ch^2 + (ch^2 - 1)*r^4 + (a^2*ch^4 - a^2)*r^2 - 2*(a^2*ch^4 - 2*a^2*ch^2 + a^2)*r)/(a^2*ch^2 + r^2)

Setting the default chart and frame

In [19]:
M.set_default_chart(RP)

In [20]:
M.set_default_frame(RP.frame())

Calculating the tensors

In [21]:
%time Riem = g.riemann()

CPU times: user 4.01 s, sys: 398 ms, total: 4.41 s
Wall time: 35.1 s


In [22]:
%time Ric = g.ricci()

CPU times: user 2.4 s, sys: 24.3 ms, total: 2.42 s
Wall time: 1.74 s


In [23]:
Ric == 0

True

In [24]:
%time R_up = Riem.up(g)

CPU times: user 1.55 s, sys: 157 ms, total: 1.7 s
Wall time: 21.8 s


In [25]:
%time R_down = Riem.down(g)

CPU times: user 436 ms, sys: 49.1 ms, total: 485 ms
Wall time: 3.31 s


In [26]:
%time Kretschmann_scalar = R_up['^{abcd}']*R_down['_{abcd}']

CPU times: user 26.8 s, sys: 358 ms, total: 27.1 s
Wall time: 22.4 s


In [27]:
Kretschmann_scalar.display()

M → ℝ
(t, r, th, ph) ↦ -48*(a^6*cos(th)^6 - 15*a^4*r^2*cos(th)^4 + 15*a^2*r^4*cos(th)^2 - r^6)/(a^12*cos(th)^12 + 6*a^10*r^2*cos(th)^10 + 15*a^8*r^4*cos(th)^8 + 20*a^6*r^6*cos(th)^6 + 15*a^4*r^8*cos(th)^4 + 6*a^2*r^10*cos(th)^2 + r^12)
(t, r, ch, ph) ↦ -48*(a^6*ch^6 - 15*a^4*ch^4*r^2 + 15*a^2*ch^2*r^4 - r^6)/(a^12*ch^12 + 6*a^10*ch^10*r^2 + 15*a^8*ch^8*r^4 + 20*a^6*ch^6*r^6 + 15*a^4*ch^4*r^8 + 6*a^2*ch^2*r^10 + r^12)

Getting and factoring the symbolic expression in the default chart

In [28]:
K_scalar = Kretschmann_scalar.expr().factor()
K_scalar

-48*(a^2*ch^2 + 4*a*ch*r + r^2)*(a^2*ch^2 - 4*a*ch*r + r^2)*(a*ch + r)*(a*ch - r)/(a^2*ch^2 + r^2)^6

### Kretschmann scalar along the singular ring, horizons and ergosurfaces

Singular Ring $(r=0,\chi=0)$

In [29]:
K_scalar.subs(r=0)

-48/(a^6*ch^6)

In [30]:
K_scalar.subs(ch=0)

48/r^6

Outer ergosurface, outer horizon and inner horizon at $\chi = 0$

In [31]:
for k in ['outer_ergo','outer_horizon','inner_horizon']:
    print(k)
    display(K_scalar.subs(eval(k)).subs({cos(th):ch}).subs(ch=0))

outer_ergo


3/4

outer_horizon


48/(sqrt(-a^2 + 1) + 1)^6

inner_horizon


48/(sqrt(-a^2 + 1) - 1)^6

Inner ergosurface for $\chi \neq 0$ (the inner ergosurface coincides with the singular ring at $\chi = 0$)

In [32]:
K_inner_ergo = K_scalar.subs(inner_ergo).subs({cos(th):ch}).canonicalize_radical()
K_inner_ergo

6*(4*a^6*ch^6 - 21*a^4*ch^4 + 21*a^2*ch^2 + (12*a^4*ch^4 - 19*a^2*ch^2 + 4)*sqrt(a*ch + 1)*sqrt(-a*ch + 1) - 4)/(a^6*ch^6 - 18*a^4*ch^4 + 48*a^2*ch^2 + 2*(3*a^4*ch^4 - 16*a^2*ch^2 + 16)*sqrt(a*ch + 1)*sqrt(-a*ch + 1) - 32)

Series expansion up to $O(\chi^6)$

In [33]:
K_inner_ergo.series(ch,6)

(-48/a^6)*ch^(-6) + (252/a^4)*ch^(-4) + (-252/a^2)*ch^(-2) + 189/4 + (45/16*a^2)*ch^2 + (45/64*a^4)*ch^4 + Order(ch^6)

Setting the default chart and frame back to Boyer–Lindquist

In [34]:
M.set_default_chart(BL)
M.set_default_frame(BL.frame())

## Kerr coordinates

The Kerr original coordinates will be used as intermediate step for introducing the Kerr-Schild coordinates.

In [35]:
Kr.<u, r, th, vph> = M.chart(r'u:(-oo,+oo) r:(0,+oo) th:(0,pi):\theta vph:(-pi,pi):periodic:\varphi')

In [36]:
f(r) = r/(a^2+r^2-2*r)
assume(a<1)
F(r) = integral(f(r),r)

In [37]:
Kr_to_BL = Kr.transition_map(BL, [u-2*F(r), r, th, vph-a*F(r)])
Kr_to_BL.display()

t = u - log((r - sqrt(-a^2 + 1) - 1)/(r + sqrt(-a^2 + 1) - 1))/sqrt(-a^2 + 1) - log(a^2 + r^2 - 2*r)
r = r
th = th
ph = -1/2*a*(log((r - sqrt(-a^2 + 1) - 1)/(r + sqrt(-a^2 + 1) - 1))/sqrt(-a^2 + 1) + log(a^2 + r^2 - 2*r)) + vph

In [38]:
Kr_to_BL.inverse().display()

u = ((a^2 - 1)*t + (a^2 - 1)*log(a^2 + r^2 - 2*r) + sqrt(a + 1)*sqrt(-a + 1)*log(-(a^2 + r^2 - 2*r)/(a^2 + 2*sqrt(a + 1)*sqrt(-a + 1)*(r - 1) - r^2 + 2*r - 2)))/(a^2 - 1)
r = r
th = th
vph = 1/2*(sqrt(a + 1)*a*sqrt(-a + 1)*log(-(a^2 + r^2 - 2*r)/(a^2 + 2*sqrt(a + 1)*sqrt(-a + 1)*(r - 1) - r^2 + 2*r - 2)) + 2*(a^2 - 1)*ph + (a^3 - a)*log(a^2 + r^2 - 2*r))/(a^2 - 1)

Showing the change of frame from BL to Kerr

In [39]:
M.change_of_frame(BL.frame(),Kr.frame())[:]

[                     1 -2*r/(a^2 + r^2 - 2*r)                      0                      0]
[                     0                      1                      0                      0]
[                     0                      0                      1                      0]
[                     0 -a*r/(a^2 + r^2 - 2*r)                      0                      1]

## Surfaces in Kerr-Schild coordinates

In [40]:
KC.<u,x,y,z> = M.chart()

Change of coordinates from Kerr to Kerr-Schild

In [41]:
Kr_to_KC = Kr.transition_map(KC, [u, (r*cos(vph) - a*sin(vph))*sin(th),
                                (r*sin(vph) + a*cos(vph))*sin(th),
                                r*cos(th)])
Kr_to_KC.display()

u = u
x = (r*cos(vph) - a*sin(vph))*sin(th)
y = (a*cos(vph) + r*sin(vph))*sin(th)
z = r*cos(th)

Parametrization of the surfaces in Kerr-Schild coordinates

In [42]:
surfaces_KC = [vector([s.subs(param) for s in Kr_to_KC(u, r, th, ph)[1:]]) for param in surfaces_param]

***
Python function for generating the surfaces

In [43]:
my_color = [colormaps.Set1(k)[:3] for k in (1,4,3)]
def kerr_surfaces(surf,a_param=.99,print_labels=True, plot_points=30, mesh=True, *args, **kwargs):
    if print_labels:
        OE = text3d('Outer ergosurface',(-2,-5,1), color='gray',fontsize='150%')
        OH = text3d('Outer horizon', (-2,-5,.5), color=my_color[0], fontsize='150%')
        IH = text3d('Inner horizon',(-2,-5,0), color=my_color[1], fontsize='150%')
        IE = text3d('Inner ergosurface', (-2,-5,-0.5),color=my_color[2],fontsize='150%')
        SRing = text3d('Singular ring',(-2,-5,-1), color='red', fontsize='150%')
        a_label = text3d('a = '+str(a_param.n(digits=5)),(-2,-5,1.5), fontsize='150%')
        Ker_BH = text3d('Kerr black hole',(-2,-5,2), fontsize='180%')
        if a_param > 1: labels = OE+IE+SRing+a_label
        else: labels = OE+IE+OH+IH+SRing+a_label+Ker_BH
    else: labels = Graphics()
    ergo_outer = parametric_plot3d(surf[0].subs(a=a_param),(th,0,pi),(ph,0,7*pi/5), color='gray', mesh=mesh, 
                                 plot_points=plot_points, frame=False, *args, **kwargs)
    ergo_inner = parametric_plot3d(surf[3].subs(a=a_param),(th,0,pi),(ph,0,2*pi), color=my_color[2], mesh=mesh, 
                                 plot_points=int(.7*plot_points))
    s_ring = parametric_plot3d(surf[4].subs(a=a_param),(ph,0,2*pi), color='red', thickness=4)
    if a_param <= 1:
        h_outer = parametric_plot3d(surf[1].subs(a=a_param),(th,0,pi),(ph,0,7*pi/5), color=my_color[0], alpha=.95, 
                                     mesh=mesh, plot_points=plot_points)
        h_inner = parametric_plot3d(surf[2].subs(a=a_param),(th,0,pi),(ph,0,6*pi/5), color=my_color[1], mesh=mesh, 
                                 plot_points=int(.7*plot_points))
        plots = ergo_outer+ergo_inner+s_ring +h_outer+h_inner  
    else:  plots = ergo_outer+ergo_inner+s_ring
    return plots+labels

***

In [44]:
kerr_surfaces(surfaces_KC, .9991, viewpoint=[[-0.6557,-0.5284,-0.5394],112.41])

Graphics3d Object

Dark theme

In [45]:
kerr_surfaces(surfaces_KC, .95999, viewpoint=[[-0.6557,-0.5284,-0.5394],112.41], theme='dark')

Graphics3d Object

## Immersion in Euclidean space

We can also see the surfaces immersed in the Euclidian space $\mathbb{E}^3$.

In [46]:
E.<x,y,z> = EuclideanSpace(3)
spherical.<r, th, ph> = E.spherical_coordinates()

Differential map from Kerr coordinates to Euclidean space

In [47]:
Kr_to_E = M.diff_map(E, {(Kr, spherical): [r,th,ph]}, name='Kr_to_E', latex_name=r'\Phi_{_{\text{Kerr} \to \mathbb{E}^3}}')

In [48]:
Kr_to_E.display()

Kr_to_E: M → E^3
   (t, r, th, ph) ↦ (x, y, z) = (r*cos(ph)*sin(th), r*sin(ph)*sin(th), r*cos(th))
   (t, r, th, ph) ↦ (r, th, ph) = (r, arctan2(r*sin(th), r*cos(th)), arctan2(r*sin(ph)*sin(th), r*cos(ph)*sin(th)))
   (t, r, ch, ph) ↦ (x, y, z) = (sqrt(ch + 1)*sqrt(-ch + 1)*r*cos(ph), sqrt(ch + 1)*sqrt(-ch + 1)*r*sin(ph), ch*r)
   (t, r, ch, ph) ↦ (r, th, ph) = (r, arctan2(sqrt(ch + 1)*sqrt(-ch + 1)*r, ch*r), arctan2(sqrt(ch + 1)*sqrt(-ch + 1)*r*sin(ph), sqrt(ch + 1)*sqrt(-ch + 1)*r*cos(ph)))
   (u, r, th, vph) ↦ (x, y, z) = (r*cos(ph)*sin(th), r*sin(ph)*sin(th), r*cos(th))
   (u, r, th, vph) ↦ (r, th, ph) = (r, th, ph)

Coordinates in Euclidean space

In [49]:
coordinates = Kr_to_E(M.point((u,r,th,vph), chart=Kr)).coordinates()

Surfaces in Euclidean space

In [50]:
surfaces_E = [vector([s.subs(param) for s in coordinates]) for param in surfaces_param]

In [51]:
kerr_surfaces(surfaces_E, a=.959999, viewpoint=[[-0.8499,-0.3478,-0.396],91.88])

Graphics3d Object

## Animating the surfaces

We now create an animation by varying the parameter $a$.

In [52]:
theme = 'light' #'light' or 'dark'
frames1 = [kerr_surfaces(surfaces_KC,k, theme=theme, 
                         viewpoint=[[-0.6557,-0.5284,-0.5394],112.41]) for k in srange(0,.5,.1)]
frames2 = [kerr_surfaces(surfaces_KC,k, theme=theme, 
                         viewpoint=[[-0.6557,-0.5284,-0.5394],112.41]) for k in srange(.5,.95,.075)]
frames3 = [kerr_surfaces(surfaces_KC,k, theme=theme, 
                         viewpoint=[[-0.6557,-0.5284,-0.5394],112.41]) for k in srange(.95,.9999,.005)]
frames4 = [kerr_surfaces(surfaces_KC,k, theme=theme, 
                         viewpoint=[[-0.6557,-0.5284,-0.5394],112.41]) for k in srange(.9999,1,.000045)]
frames = frames1+frames2+frames3+frames4

In [53]:
animate(frames).interactive()

Graphics3d Object